In [1]:
# set CUDA
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "2,3"

from bertopic import BERTopic
from sentence_transformers import SentenceTransformer
from umap import UMAP
from hdbscan import HDBSCAN
from bertopic.vectorizers import ClassTfidfTransformer

import jieba
import jieba.analyse
import jieba.posseg
import re
import pandas as pd
import numpy as np

/home/chengyuli/miniconda3/envs/DL/lib/python3.8/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Data prepare
df = pd.read_csv('/home/chengyuli/yanshan/data/DataScience/UN_raw.csv')
df.head()

web-scraper-order                              web-scraper-start-url  \
0      1701845523-1  https://news.un.org/zh/tags/bayijushi?f[0]=dat...   
1      1701845523-2  https://news.un.org/zh/tags/bayijushi?f[0]=dat...   
2      1701845523-3  https://news.un.org/zh/tags/bayijushi?f[0]=dat...   
3      1701845523-4  https://news.un.org/zh/tags/bayijushi?f[0]=dat...   
4      1701845523-5  https://news.un.org/zh/tags/bayijushi?f[0]=dat...   

                                 urls  \
0        【巴以冲突第60天】加沙地带已无安全区，绝望情绪日益加剧   
1  国际刑事法院检察官首访以色列与巴勒斯坦国，强调法律必须能够保护所有人   
2           【巴以冲突第58天】人权高专呼吁结束暴力，恢复对话   
3     【巴以冲突第57天】以军轰炸造成大量人员伤亡，医疗设施不堪重负   
4      【巴以冲突第56天】战火再起，加沙满目疮痍之下重陷震惊与恐惧   

                                      urls-href        time  \
0  https://news.un.org/zh/story/2023/12/1124617  2023年12月5日   
1  https://news.un.org/zh/story/2023/12/1124607  2023年12月4日   
2  https://news.un.org/zh/story/2023/12/1124562  2023年12月3日   
3  https://news.un.org/zh/story/2023/12/1124557  2023年12月2日   
4  https://news.un.org/zh/story/2023/12/1124512  2023年12月1日   

                                            contents  
0  世界卫生组织今天表示，自哈马斯武装分子10月7日在以色列南部屠杀约1200人并劫持约240名...  
1  国际刑事法院检察官卡里姆·汗（Karim Khan）于12月2日结束了对以色列与巴勒斯坦国的...  
2  联合国人权事务高级专员蒂尔克今天表示，加沙地带重新恢复的残酷敌对行动及其对平民的可怕影响再次...  
3  联合国人道主义事务协调厅今天表示，自休战结束以来，以色列连续第二天继续从空中、陆地和海上对加...  
4  在经历连续七日的人道主义暂停之后，军事行动今天在加沙重启，联合国秘书长古特雷斯对此深表遗憾。...

In [3]:
# prepare stop words
stopwords = []

# Read in txt.
with open("/home/chengyuli/yanshan/data/DataScience/stop_words_ch.txt", "r", encoding="GBK") as f:
    stopwords = [line.strip() for line in f.readlines()]
    
print(stopwords)

['', '`', '^', '~', '<', '=', '>', '|', '_', '-', '--', ',', ';', ':', '!', '?', '/', '.', '...', "'", '"', '(', ')', '@', '$', '*', '\\', '&', '#', '%', '+', '直到', '直接', '只限', '只是', '只有', '嘎登', '分别', '现代', '抑或', '又', '等', '比', '其', '嘿', '照', '经', '乃', '啐', '呵', '｝', '６', '１', '＄', '离', '〉', '怎', '］', '乎', '用', '８', '～', '＃', '的', '呜', '就', '嗳', '哉', '＊', '彼', '趁', '喏', '、', '︿', '此', '咳', '八', '啦', '们', '那', '朝', '管', '沿', '本', '归', '呃', '宁', '者', '几', '到', '嘛', '咚', '５', '五', '哇', '“', '＜', '所', '唉', '因', '之', '个', '二', '别', '’', '凭', '由', '啊', '＋', '拿', '嗯', '有', '给', '在', '）', '哪', '连', '哼', '且', '俺', '您', '｜', '你', '向', '这', '和', '起', '０', '〈', '往', '她', '依', '九', '；', '任', '啥', '—', '哎', '得', '焉', '七', '', '随', '呸', '顺', '较', '地', '｛', '借', '像', '４', '则', '何', '》', '纵', '另', '？', '各', '［', '＆', '‘', '哈', '自', '！', '阿', '矣', '零', '能', '咱', '吧', '当', '哩', '（', '于', '按', '对', '据', '若', '边', '三', '嘎', '打', '３', '它', '：', '吱', '而', '％', '呢', '，', '来', '以', '但', '至', '着', '倘', '呗', '将'

In [4]:
# filter text and transfer to list.
raw_text = df['contents'].tolist()
print(raw_text)

['世界卫生组织今天表示，自哈马斯武装分子10月7日在以色列南部屠杀约1200人并劫持约240名人质以来，以色列对加沙发动了历来最猛烈的炮击作为报复，加沙民众的处境由此每况愈下。他通过视频连线在日内瓦对记者说：“加沙局势每小时都在恶化。各地遭受的轰炸都在加紧，包括汗尤尼斯和拉法等南部地区。”皮佩尔科恩指出，在过去几天里，越来越多的境内流离失所者担心自己的生命安全，纷纷从加沙中部甚至南部离开。联合国儿童基金会发言人埃尔德（James Elder）也表达了同样的担忧。他强调，国际人道法规定军队有义务“采取一切可行措施”保护平民；单方面宣布平民应前往所谓的安全区是不可接受的，因为这些安全区实际上是没有水、住所或卫生设施的人行道或半成品建筑。埃尔德说：“如果只是免于轰炸，那就不算是安全区，甚至有些称为安全区的地方都遭到了轰炸。”人道协调厅在其最新的紧急状况更新中指出，据以色列消息来源称，三名以色列士兵被打死。近东救济工程处表示，近120万境内流离失所者在该机构位于加沙地带所有五个省（包括北部省和加沙城）的156个设施中找到了栖身之所。经近东救济工程处证实，最近该机构工作人员在空袭中丧生的人数至少新增了19名，使10月7日以来遇难的联合国人员总数达到130人。该机构援引顾问杰汉（Jehan）的话说：“我们走在路上也很危险，我们的生活被按下了暂停键……这里弥漫着死亡的气息，但我们决心要活下去。”加沙卫生当局估计，在本轮巴以冲突中，加沙至少有1.6万名巴勒斯坦人丧生，其中70%据信是妇女和儿童。近东救济工程处表示，还有更多的人失踪，他们可能被埋在废墟之下，等待救援或搜寻。在人道主义物资严重短缺的情况下，人道协调厅报告说，上周末每天约有100辆援助卡车和6.9万升燃料抵达加沙，但这仍远远低于11月24日至30日战事暂停期间平均每天170辆卡车和11万升燃料的运送量。皮佩尔科恩说：“这援助量太少了，实在少得可怜，面临加沙日益加剧的灾难，需要更多的药品、粮食、水和燃料。”皮佩尔科恩表示，加沙的医疗基础设施近乎瘫痪，北部几乎没有任何正常运作的医疗设施，只有阿赫利阿拉伯医院人满为患，接收了大量外伤病患，但也缺乏医疗用品。而且，同样绝望的场景还可能在南部重演，皮佩尔科恩对此深表关切。他解释说，在10月7日冲突升级之前，加沙有3500张病床，而现在只有1500张。他说：“放眼望去，加沙北部的医

In [5]:
# Data clearing
new_text = []
for line in raw_text:
    if (line != ''):
        line = line.strip()
        # 去除文本中的英文和数字
        line = re.sub("[a-zA-Z0-9]", "", line)
        # 去除文本中的中文符号和英文符号
        line = re.sub("[\s+\.\!\/_,$%^*(+\"\'；：“”．]+|[+——！，。？?、~@#￥%……&*（）‘’]+", "", line)
    new_text.append(line)
print(new_text)

['世界卫生组织今天表示自哈马斯武装分子月日在以色列南部屠杀约人并劫持约名人质以来以色列对加沙发动了历来最猛烈的炮击作为报复加沙民众的处境由此每况愈下他通过视频连线在日内瓦对记者说加沙局势每小时都在恶化各地遭受的轰炸都在加紧包括汗尤尼斯和拉法等南部地区皮佩尔科恩指出在过去几天里越来越多的境内流离失所者担心自己的生命安全纷纷从加沙中部甚至南部离开联合国儿童基金会发言人埃尔德也表达了同样的担忧他强调国际人道法规定军队有义务采取一切可行措施保护平民单方面宣布平民应前往所谓的安全区是不可接受的因为这些安全区实际上是没有水住所或卫生设施的人行道或半成品建筑埃尔德说如果只是免于轰炸那就不算是安全区甚至有些称为安全区的地方都遭到了轰炸人道协调厅在其最新的紧急状况更新中指出据以色列消息来源称三名以色列士兵被打死近东救济工程处表示近万境内流离失所者在该机构位于加沙地带所有五个省包括北部省和加沙城的个设施中找到了栖身之所经近东救济工程处证实最近该机构工作人员在空袭中丧生的人数至少新增了名使月日以来遇难的联合国人员总数达到人该机构援引顾问杰汉的话说我们走在路上也很危险我们的生活被按下了暂停键这里弥漫着死亡的气息但我们决心要活下去加沙卫生当局估计在本轮巴以冲突中加沙至少有万名巴勒斯坦人丧生其中据信是妇女和儿童近东救济工程处表示还有更多的人失踪他们可能被埋在废墟之下等待救援或搜寻在人道主义物资严重短缺的情况下人道协调厅报告说上周末每天约有辆援助卡车和万升燃料抵达加沙但这仍远远低于月日至日战事暂停期间平均每天辆卡车和万升燃料的运送量皮佩尔科恩说这援助量太少了实在少得可怜面临加沙日益加剧的灾难需要更多的药品粮食水和燃料皮佩尔科恩表示加沙的医疗基础设施近乎瘫痪北部几乎没有任何正常运作的医疗设施只有阿赫利阿拉伯医院人满为患接收了大量外伤病患但也缺乏医疗用品而且同样绝望的场景还可能在南部重演皮佩尔科恩对此深表关切他解释说在月日冲突升级之前加沙有张病床而现在只有张他说放眼望去加沙北部的医院几乎完全停摆这就是我们所目睹的北部的情况我们深感关切的是这种情况不能也不应该在加沙南部上演皮佩尔科恩还指出医疗用品已于周日从汗尤尼斯的两个仓库转移到拉法这是因为有建议称仓库所在地的居民被要求撤离未来几天该地区很可能会战事频发联合国世界粮食计划署今天发表声明表示加沙敌对行动的恢复只会加剧灾难性的饥饿危机让加沙平民更加不堪

In [6]:
# Turn to datetime from string pattern.
time = df['time']
ymd = ['{}-{}-{}'.format(re.split('年|月|日', i)[0], re.split('年|月|日', i)[1], re.split('年|月|日', i)[2]) for i in time]
ymd = pd.to_datetime(ymd)
df['time'] = ymd
print(ymd.tolist())

[Timestamp('2023-12-05 00:00:00'), Timestamp('2023-12-04 00:00:00'), Timestamp('2023-12-03 00:00:00'), Timestamp('2023-12-02 00:00:00'), Timestamp('2023-12-01 00:00:00'), Timestamp('2023-11-30 00:00:00'), Timestamp('2023-11-29 00:00:00'), Timestamp('2023-11-29 00:00:00'), Timestamp('2023-11-29 00:00:00'), Timestamp('2023-11-28 00:00:00'), Timestamp('2023-11-28 00:00:00'), Timestamp('2023-11-27 00:00:00'), Timestamp('2023-11-27 00:00:00'), Timestamp('2023-11-26 00:00:00'), Timestamp('2023-11-25 00:00:00'), Timestamp('2023-11-24 00:00:00'), Timestamp('2023-11-24 00:00:00'), Timestamp('2023-11-23 00:00:00'), Timestamp('2023-11-22 00:00:00'), Timestamp('2023-11-22 00:00:00'), Timestamp('2023-11-21 00:00:00'), Timestamp('2023-11-20 00:00:00'), Timestamp('2023-11-20 00:00:00'), Timestamp('2023-11-19 00:00:00'), Timestamp('2023-11-18 00:00:00'), Timestamp('2023-11-17 00:00:00'), Timestamp('2023-11-17 00:00:00'), Timestamp('2023-11-16 00:00:00'), Timestamp('2023-11-16 00:00:00'), Timestamp('20

In [7]:
# 文本切割并仅保留名词
jieba.suggest_freq(('人权', '人道', '人民', '人口'), tune=True)
filtered_text = []
for line in new_text:
    segList = jieba.posseg.cut(line)
    segSentence = ''
    for x in segList:
        if x.flag in ['n'] and x.word != '\t':
            segSentence += x.word + ' '
    filtered_text.append(segSentence)
print(filtered_text)

Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache


Loading model cost 1.502 seconds.
Prefix dict has been built successfully.


['武装 分子 人质 民众 处境 视频 连线 记者 局势 小时 汗 地区 皮 流离失所 国际 人道 法 规定 军队 义务 措施 平民 单方面 平民 水 住所 卫生设施 人行道 半成品 建筑 地方 人 厅 消息来源 士兵 近东 救济 工程处 流离失所 机构 地带 省 省 个 设施 经 近东 救济 工程处 证实 机构 工作人员 人数 人员 总数 人 机构 键 气息 当局 信是 妇女 儿童 近东 救济 工程处 人 废墟 人道主义 物资 情况 人 厅 报告 上周末 卡车 燃料 战事 卡车 燃料 量 皮 量 日益加剧 灾难 药品 粮食 水 燃料 皮 医疗 基础设施 医疗 设施 医院 大量 外伤 病患 医疗 用品 场景 皮 深表 病床 医院 情况 情况 皮 医疗 用品 汗 仓库 建议 仓库 所在地 居民 地区 战事 敌对行动 灾难性 饥饿 危机 平民 粮食 合作伙伴 数量 粮食 无法 地方 地区 时间 内 粮食 人 粮食 机构 战火 物资 无法 人道主义 工作者 平民 灾难 粮食 命脉 粮食 国际 人道 法 规定 义务 人道主义 工作者 物资 持久和平 人道主义 灾难 粮食 人道主义 领导人 紧迫感 政治 解决方案 悲剧 家庭 国际 法院 检察官 汗 实地 法院 历史 检察官 两地 行程 时 时候 法律 检察官 办公室 所有人 法律 被占领土 危机 大量 平民 人权 专家 战争 罪 危害 人类 追究责任 平民 国际法 义务 ', '国际 法院 检察官 汗 实地 法院 历史 检察官 两地 行程 时 时候 法律 检察官 办公室 所有人 法律 性质 双方 受害者 遭遇 经历 受害者 话语 时刻 人性 核心 部分 大量 公民 武装 团体 人质 受害者 亲友 贝 基布 卡法 基布 社区 音乐节 现场 经 精心策划 景象 无辜 平民 国际 罪行 罪行 人类 良知 国际 法院 罪行 汗 会见 受害者 家属 时 信息 国际 法院 问责 规约 核心 互补性 原则 国家 当局 所有人 儿童 人性 基本 原则 人质 人体 盾牌 筹码 权力 机构 总部 所在地 会见 总统 总理 司法部长 勒代 汗 受害者 家属 对话 个人经历 问题 明确指出 地带 武装 团体 国际 人道 法 方式 武装冲突 法律 框架 人口稠密 地区 战斗人员 指 平民 时 复杂性 国际 人道 法 军方 法律 法律 区分 性 原则 

In [8]:
# Step 1 - Embed documents
embedding_model = SentenceTransformer("/home/chengyuli/yanshan/data/HuggingFace/paraphrase-multilingual-MiniLM-L12-v2")

In [9]:
# Step 2 - Reduce dimensionality
umap_model = UMAP(n_neighbors=15, n_components=2, min_dist=0.0, metric='cosine')

In [10]:
# Step 3 - Cluster reduced embeddings
hdbscan_model = HDBSCAN(min_cluster_size=5, metric='euclidean', cluster_selection_method='eom', prediction_data=True)

In [11]:
# Step 4 - Tokenize topics
from sklearn.feature_extraction.text import CountVectorizer

vectorizer_model = CountVectorizer(stop_words=stopwords)

In [12]:
# Step 5 - Create topic representation
ctfidf_model = ClassTfidfTransformer()

In [13]:
# All steps together
topic_model = BERTopic(
  embedding_model=embedding_model,    # Step 1 - Extract embeddings
  umap_model=umap_model,              # Step 2 - Reduce dimensionality
  hdbscan_model=hdbscan_model,        # Step 3 - Cluster reduced embeddings
  vectorizer_model=vectorizer_model,  # Step 4 - Tokenize topics
  ctfidf_model=ctfidf_model,          # Step 5 - Extract topic words
  nr_topics='none',
  top_n_words=10
)

In [14]:
# train and save the model.
topics, probabilities = topic_model.fit_transform(filtered_text)

# save model
topic_model.save("/home/chengyuli/yanshan/data/DataScience/BERTopic", serialization="safetensors")

In [17]:
# Load the model
topic_model = BERTopic.load("/home/chengyuli/yanshan/data/DataScience/BERTopic",
                            embedding_model=embedding_model)

2023-12-13 17:58:54,785 - BERTopic - WARNING: You are loading a BERTopic model without explicitly defining an embedding model.If you want to also load in an embedding model, make sure to useBERTopic.load(my_model, embedding_model=my_embedding_model).


In [15]:
topic_model.get_document_info(filtered_text)

Document  Topic  \
0   武装 分子 人质 民众 处境 视频 连线 记者 局势 小时 汗 地区 皮 流离失所 国际 人...      0   
1   国际 法院 检察官 汗 实地 法院 历史 检察官 两地 行程 时 时候 法律 检察官 办公室...     -1   
2   人权 事务 地带 敌对行动 平民 暴力 协议 深表 平民 无法 暴力 解决办法 枪声 平息 ...     -1   
3   人道主义 事务 厅 陆地 地面 事件 时分 难民营 楼房 流离失所 人 信 人 废墟 小时 ...      0   
4   经历 人道主义 军事行动 秘书长 人道主义 工作人员 人 战火 飞 地方 人道主义 燃料 食...      2   
..                                                ...    ...   
86  关键 体 平民 危机 暴力 人口 食品 水 全面 地面 办公室 重大损失 机构 地方 平民 ...      2   
87  人道主义 机构 警告 粮食 水电 关键 物资 飞 居民 无法 流离失所 近东 难民 救济 工...     -1   
88  关键 行动者 会议 人员 边境 火箭弹 炮火 地带 总部 近东 难民 救济 工程处 报告 巨...      2   
89  平民 暴力 被占领土 地带 持枪 地带 火箭弹 时据 人 人 秘书长 时间 措辞 地带 地区...     -1   
90  进程 协调员 无情 定居点 进程 协调员 大使 住房 定居点 助长 暴力 土地 资源 系统性...     -1   

                Name                               Representation  \
0   0_医院_人道主义_救济_工程处  [医院, 人道主义, 救济, 工程处, 近东, 平民, 医疗, 儿童, 地带, 物资]   
1   -1_平民_国际_人道主义_地区  [平民, 国际, 人道主义, 地区, 人权, 暴力, 定居者, 儿童, 人民, 局势]   
2   -1_平民_国际_人道主义_地区  [平民, 国际, 人道主义, 地区, 人权, 暴力, 定居者, 儿童, 人民, 局势]   
3   0_医院_人道主义_救济_工程处  [医院, 人道主义, 救济, 工程处, 近东, 平民, 医疗, 儿童, 地带, 物资]   
4    2_人道主义_儿童_救济_近东  [人道主义, 儿童, 救济, 近东, 工程处, 妇女, 专家, 医院, 机构, 物资]   
..               ...                                          ...   
86   2_人道主义_儿童_救济_近东  [人道主义, 儿童, 救济, 近东, 工程处, 妇女, 专家, 医院, 机构, 物资]   
87  -1_平民_国际_人道主义_地区  [平民, 国际, 人道主义, 地区, 人权, 暴力, 定居者, 儿童, 人民, 局势]   
88   2_人道主义_儿童_救济_近东  [人道主义, 儿童, 救济, 近东, 工程处, 妇女, 专家, 医院, 机构, 物资]   
89  -1_平民_国际_人道主义_地区  [平民, 国际, 人道主义, 地区, 人权, 暴力, 定居者, 儿童, 人民, 局势]   
90  -1_平民_国际_人道主义_地区  [平民, 国际, 人道主义, 地区, 人权, 暴力, 定居者, 儿童, 人民, 局势]   

                                  Representative_Docs  \
0   [主管 人道主义 事务 秘书长 救济 协调员 格 程度 代表 国际 人道主义 界 计划 人性...   
1   [人权 事务 人道主义 被劫持 人质 民众 噩梦般 处境 一览 时间 人 厅 情况 报告 人...   
2   [人权 事务 人道主义 被劫持 人质 民众 噩梦般 处境 一览 时间 人 厅 情况 报告 人...   
3   [主管 人道主义 事务 秘书长 救济 协调员 格 程度 代表 国际 人道主义 界 计划 人性...   
4   [人道主义 机构 生效 物资 卡车 拉法 人道主义 事务 厅 暴力 地区 海陆空 武装 团体...   
..                                                ...   
86  [人道主义 机构 生效 物资 卡车 拉法 人道主义 事务 厅 暴力 地区 海陆空 武装 团体...   
87  [人权 事务 人道主义 被劫持 人质 民众 噩梦般 处境 一览 时间 人 厅 情况 报告 人...   
88  [人道主义 机构 生效 物资 卡车 拉法 人道主义 事务 厅 暴力 地区 海陆空 武装 团体...   
89  [人权 事务 人道主义 被劫持 人质 民众 噩梦般 处境 一览 时间 人 厅 情况 报告 人...   
90  [人权 事务 人道主义 被劫持 人质 民众 噩梦般 处境 一览 时间 人 厅 情况 报告 人...   

                                          Top_n_words  Probability  \
0   医院 - 人道主义 - 救济 - 工程处 - 近东 - 平民 - 医疗 - 儿童 - 地带 ...     0.665087   
1   平民 - 国际 - 人道主义 - 地区 - 人权 - 暴力 - 定居者 - 儿童 - 人民 ...     0.000000   
2   平民 - 国际 - 人道主义 - 地区 - 人权 - 暴力 - 定居者 - 儿童 - 人民 ...     0.000000   
3   医院 - 人道主义 - 救济 - 工程处 - 近东 - 平民 - 医疗 - 儿童 - 地带 ...     0.906459   
4   人道主义 - 儿童 - 救济 - 近东 - 工程处 - 妇女 - 专家 - 医院 - 机构 ...     0.996804   
..                                                ...          ...   
86  人道主义 - 儿童 - 救济 - 近东 - 工程处 - 妇女 - 专家 - 医院 - 机构 ...     1.000000   
87  平民 - 国际 - 人道主义 - 地区 - 人权 - 暴力 - 定居者 - 儿童 - 人民 ...     0.000000   
88  人道主义 - 儿童 - 救济 - 近东 - 工程处 - 妇女 - 专家 - 医院 - 机构 ...     1.000000   
89  平民 - 国际 - 人道主义 - 地区 - 人权 - 暴力 - 定居者 - 儿童 - 人民 ...     0.000000   
90  平民 - 国际 - 人道主义 - 地区 - 人权 - 暴力 - 定居者 - 儿童 - 人民 ...     0.000000   

    Representative_document  
0                     False  
1                     False  
2                     False  
3                     False  
4                     False  
..                      ...  
86                     True  
87                    False  
88                    False  
89                    False  
90                    False  

[91 rows x 8 columns]

In [16]:
topic_model.get_topic_freq()

Topic  Count
0      0     33
1     -1     21
3      1     18
2      2     12
4      3      7

In [17]:
topic_model.get_topic(0)

[('医院', 0.08289696939367672),
 ('人道主义', 0.06079846468710149),
 ('救济', 0.05681320359808606),
 ('工程处', 0.05227452005857994),
 ('近东', 0.05031351995962309),
 ('平民', 0.04837261375533403),
 ('医疗', 0.045038649140820224),
 ('儿童', 0.0416928955368665),
 ('地带', 0.041608727148896706),
 ('物资', 0.03825930261191281)]

In [18]:
topic_model.visualize_barchart()

In [19]:
embeddings = embedding_model.encode(filtered_text, show_progress_bar=False)

# Run the visualization with the original embeddings
topic_model.visualize_documents(filtered_text, embeddings=embeddings)

In [20]:
topic_model.visualize_hierarchy()

In [21]:
topic_model.visualize_heatmap()

In [22]:
topic_model.visualize_topics()

In [23]:
# Build DTM
topics_over_time = topic_model.topics_over_time(docs=filtered_text,
                                               timestamps=ymd.tolist(),
                                               global_tuning=True,
                                               evolution_tuning=True,
                                               nr_bins=7)

print(topics_over_time)

    Topic                   Words  Frequency                     Timestamp
0      -1    定居点, 进程, 协调员, 土地, 通报          1 2023-09-26 22:20:38.400000000
1      -1    平民, 地带, 人道主义, 国际, 人权          3 2023-10-06 20:34:17.142857216
2       0   救济, 人道主义, 医院, 工程处, 平民          2 2023-10-06 20:34:17.142857216
3       1      草案, 决议, 代表, 平民, 投票          1 2023-10-06 20:34:17.142857216
4       2   救济, 近东, 工程处, 人道主义, 部队          3 2023-10-06 20:34:17.142857216
5      -1    平民, 人道主义, 草案, 国际, 决议          3 2023-10-16 17:08:34.285714176
6       0    医院, 医疗, 人道主义, 救济, 平民          6 2023-10-16 17:08:34.285714176
7       1    草案, 决议, 平民, 人道主义, 会议          7 2023-10-16 17:08:34.285714176
8       3     救济, 近东, 工程处, 燃料, 物资          3 2023-10-16 17:08:34.285714176
9      -1    定居者, 委员会, 儿童, 平民, 事件          4 2023-10-26 13:42:51.428571392
10      0   医院, 人道主义, 救济, 平民, 工程处         10 2023-10-26 13:42:51.428571392
11      1    决议, 草案, 平民, 人道主义, 代表          3 2023-10-26 13:42:51.428571392
12      3   燃料, 粮食, 人道主义,

In [24]:
# Visualize DTM
topic_model.visualize_topics_over_time(topics_over_time, top_n_topics=10)